# Overview:

In this notebook, you will see demo of how [Redshift Spectrum](https://docs.aws.amazon.com/redshift/latest/dg/c-getting-started-using-spectrum.html) features helps to query data in S3.  Also analyze data from both local table in your data warehouse and extenral data in data lake using single query.

## Use case
Let us consider you have web_sales data in your data lake on an S3 location.  

You need to analyze web sales data by year. Your date dimension table (date_dim) is stored in the data warehouse.  So you need to combine these two datasets for analysi.  

Let us see how you can do that using Redshift spectrum.

## Pre-requisites
1. Create Amazon Redshift cluster - https://docs.aws.amazon.com/redshift/latest/gsg/rs-gsg-launch-sample-cluster.html
    
    Note: You can also demo this on [Redshift Serverless](https://docs.aws.amazon.com/redshift/latest/gsg/new-user-serverless.html#serverless-console-resource-creation)
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

## Create external schema and tables pointing data in S3

Let us create external schema & table pointing to that location.

In [0]:
--Creating external schema and Glue catalog database
create external schema ext_tpcds_s3
from data catalog
database ext_tpcds_db
iam_role default
create external database if not exists;


--Create External tables pointing to data in S3.
CREATE EXTERNAL TABLE ext_tpcds_s3.web_sales
(
 ws_sold_date_sk int4 ,             
  ws_sold_time_sk int4 ,        
  ws_ship_date_sk int4 ,        
  ws_item_sk int4  ,    
  ws_bill_customer_sk int4 ,    
  ws_bill_cdemo_sk int4 ,       
  ws_bill_hdemo_sk int4 ,       
  ws_bill_addr_sk int4 ,        
  ws_ship_customer_sk int4 ,    
  ws_ship_cdemo_sk int4 ,       
  ws_ship_hdemo_sk int4 ,       
  ws_ship_addr_sk int4 ,        
  ws_web_page_sk int4 ,         
  ws_web_site_sk int4 ,         
  ws_ship_mode_sk int4 ,        
  ws_warehouse_sk int4 ,        
  ws_promo_sk int4 ,            
  ws_order_number int8 ,
  ws_quantity int4 ,            
  ws_wholesale_cost numeric(7,2) ,                
  ws_list_price numeric(7,2) ,  
  ws_sales_price numeric(7,2) , 
  ws_ext_discount_amt numeric(7,2) ,              
  ws_ext_sales_price numeric(7,2) ,
  ws_ext_wholesale_cost numeric(7,2) ,               
  ws_ext_list_price numeric(7,2) , 
  ws_ext_tax numeric(7,2) ,     
  ws_coupon_amt numeric(7,2) ,  
  ws_ext_ship_cost numeric(7,2) ,                 
  ws_net_paid numeric(7,2) ,    
  ws_net_paid_inc_tax numeric(7,2) ,              
  ws_net_paid_inc_ship numeric(7,2) ,             
  ws_net_paid_inc_ship_tax numeric(7,2) ,         
  ws_net_profit numeric(7,2)
)
row format delimited
fields terminated by '|'
stored as textfile
LOCATION 's3://redshift-downloads/TPC-DS/2.13/1TB/web_sales/';

## Query data in S3 to validate

In [0]:
select * from ext_tpcds_s3.web_sales limit 10;

## Create and load date_dim table locally in your data warehouse

In [0]:
create table date_dim
(
    d_date_sk                 integer               not null,
    d_date_id                 char(16)              not null,
    d_date                    date,
    d_month_seq               integer                       ,
    d_week_seq                integer                       ,
    d_quarter_seq             integer                       ,
    d_year                    integer                       ,
    d_dow                     integer                       ,
    d_moy                     integer                       ,
    d_dom                     integer                       ,
    d_qoy                     integer                       ,
    d_fy_year                 integer                       ,
    d_fy_quarter_seq          integer                       ,
    d_fy_week_seq             integer                       ,
    d_day_name                char(9)                       ,
    d_quarter_name            char(6)                       ,
    d_holiday                 char(1)                       ,
    d_weekend                 char(1)                       ,
    d_following_holiday       char(1)                       ,
    d_first_dom               integer                       ,
    d_last_dom                integer                       ,
    d_same_day_ly             integer                       ,
    d_same_day_lq             integer                       ,
    d_current_day             char(1)                       ,
    d_current_week            char(1)                       ,
    d_current_month           char(1)                       ,
    d_current_quarter         char(1)                       ,
    d_current_year            char(1)                       ,
    primary key (d_date_sk)
) diststyle all;

copy date_dim from 's3://redshift-downloads/TPC-DS/2.13/1TB/date_dim/' iam_role default gzip delimiter '|' EMPTYASNULL region 'us-east-1';

## Run single query combining data in S3 (web_sales) and data in your data warehouse (date_dim)

In [0]:
select d_year AS ws_sold_year, ws_item_sk,    ws_bill_customer_sk
     ws_customer_sk,    sum(ws_quantity) ws_qty,    sum(ws_wholesale_cost) ws_wc,
        sum(ws_sales_price) ws_sp   
from ext_tpcds_s3.web_sales join date_dim on ws_sold_date_sk = d_date_sk   
group by d_year, ws_item_sk, ws_bill_customer_sk

## Cleanup

Please delete the Redshift cluster to avoid unnecessary costs. https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#delete-cluster

Thank you for using this notebook.  Please share your feedback to redshift-specialists-amer@amazon.com